In [34]:
import altair as alt
import altair_catplot as altcat
import pandas as pd
from vega_datasets import data
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [35]:
df = pd.read_csv('datasets/MHV_MHI.csv')
df

County_State             County     State  Median_HV  \
0        Autauga County, Alabama     Autauga County   Alabama     127400   
1        Baldwin County, Alabama     Baldwin County   Alabama     164400   
2        Barbour County, Alabama     Barbour County   Alabama      95550   
3           Bibb County, Alabama        Bibb County   Alabama      92100   
4         Blount County, Alabama      Blount County   Alabama     114050   
...                          ...                ...       ...        ...   
3089  Sweetwater County, Wyoming  Sweetwater County   Wyoming     182250   
3090       Teton County, Wyoming       Teton County   Wyoming     741750   
3091       Uinta County, Wyoming       Uinta County   Wyoming     174350   
3092    Washakie County, Wyoming    Washakie County   Wyoming     157200   
3093      Weston County, Wyoming      Weston County   Wyoming     176800   

      Median_HI  
0       55745.0  
1       56955.0  
2       45771.5  
3       44451.5  
4       52026.0  
...         ...  
3089    76566.5  
3090    91873.5  
3091    67358.0  
3092    56175.0  
3093    66506.5  

[3094 rows x 5 columns]

In [36]:
df['MHV_MHI_Ratio'] = df['Median_HV']/df['Median_HI']
df = df.round(2)
df

County_State             County     State  Median_HV  \
0        Autauga County, Alabama     Autauga County   Alabama     127400   
1        Baldwin County, Alabama     Baldwin County   Alabama     164400   
2        Barbour County, Alabama     Barbour County   Alabama      95550   
3           Bibb County, Alabama        Bibb County   Alabama      92100   
4         Blount County, Alabama      Blount County   Alabama     114050   
...                          ...                ...       ...        ...   
3089  Sweetwater County, Wyoming  Sweetwater County   Wyoming     182250   
3090       Teton County, Wyoming       Teton County   Wyoming     741750   
3091       Uinta County, Wyoming       Uinta County   Wyoming     174350   
3092    Washakie County, Wyoming    Washakie County   Wyoming     157200   
3093      Weston County, Wyoming      Weston County   Wyoming     176800   

      Median_HI  MHV_MHI_Ratio  
0       55745.0           2.29  
1       56955.0           2.89  
2       45771.5           2.09  
3       44451.5           2.07  
4       52026.0           2.19  
...         ...            ...  
3089    76566.5           2.38  
3090    91873.5           8.07  
3091    67358.0           2.59  
3092    56175.0           2.80  
3093    66506.5           2.66  

[3094 rows x 6 columns]

In [37]:
#### Vis1 - Median Home Value and Median Household Income county distribution

# Dropdown Selection (State)
state_list = df['State'].unique().tolist()
selectState = alt.selection_single(
    fields = ['State'],
    name = 'State ',
    bind = alt.binding_select(options = [None] + state_list, labels = ['All'] + state_list, name = 'State ')
)

selection = alt.selection_single(on = 'mouseover',empty = 'none')

# Scatter Plot
scatter_plot = alt.Chart(
    data = df,
    width = 600, 
    height = 500
).encode(
    alt.X('Median_HI:Q', axis = alt.Axis(format = '~s', titleFontSize = 14), scale=alt.Scale(domain=[10000, 130000])),
    alt.Y('Median_HV:Q', axis = alt.Axis(format = '~s', titleFontSize = 14), scale=alt.Scale(domain=[0, 800000])),
    tooltip = [alt.Tooltip('State:N'),
               alt.Tooltip('County:N'),
               alt.Tooltip('Median_HV:Q', title = 'Median Home Value'),
               alt.Tooltip('Median_HI:Q', title = 'Median Household Income'),
               alt.Tooltip('MHV_MHI_Ratio:Q', title = 'MHV/MHI Ratio Ratio')]
)

# All points
all_points = scatter_plot.mark_point(
    color = 'white', 
    fill = 'lightgray',
    strokeWidth = 0.8,
    opacity = 0.6,
    size = 90).add_selection(
    selectState
)

point_highlight = scatter_plot.mark_point(
    color = 'white', 
    fill = '#55b9cf',
    strokeWidth = 0.8,
    opacity = 0.6,
    size = 90).transform_filter(selectState).add_selection(
    selection
).encode(
    color = alt.condition(selection, alt.value('black'), alt.value('white'))
)

# Red Lake County
RL_point = scatter_plot.mark_point(
    color = 'white',
    fill = '#dd4b5f',
    strokeWidth = 0.8,
    size = 120
).transform_filter(
alt.datum.County == 'Red Lake County'
)

# Red Lake County Annotation
annotation = alt.Chart(df).mark_text(
    align = 'left',
    baseline = 'middle',
    fontSize = 16,
    color = '#dd4b5f',
    dx = 15
).encode(
    alt.X('Median_HI:Q'),
    alt.Y('Median_HV:Q'),
    text = 'County_State'
).transform_filter(
    alt.datum.County == 'Red Lake County'
)

# Top Histogram
top_hist = alt.Chart(
    data = df,
    width = 600,
    height = 85
).mark_bar(color = '#55b9cf', opacity = 0.6).encode(
    alt.X('Median_HI:Q', 
          bin = alt.Bin(maxbins = 50, extent = alt.Scale(domain=(10000, 130000)).domain), 
          title = None,
          axis=alt.Axis(labels=False, tickSize = 0, domainOpacity = 0.4)),
    alt.Y('count()', 
          title = '', 
          axis = alt.Axis(grid = False, labels=False, tickSize = 0, domainOpacity = 0))
).transform_filter(selectState)

# Right Histogram
right_hist = alt.Chart(
    data = df,
    width = 85,
    height = 500
).mark_bar(color = '#55b9cf', opacity = 0.6).encode(
    alt.X('count()', 
          title = '', 
          axis = alt.Axis(grid = False, labels=False, tickSize = 0, domainOpacity = 0)),
    alt.Y('Median_HV:Q', 
          bin = alt.Bin(maxbins = 40, extent = alt.Scale(domain=(0, 800000)).domain), 
          title = None,
          axis=alt.Axis(labels = False, tickSize = 0, domainOpacity = 0.4))
).transform_filter(selectState)

# Vertical & Horizontal Lines
avg_MHI = alt.Chart(df).mark_rule(strokeDash=[4,4], opacity = 0.8).encode(alt.X('mean(Median_HI):Q', title = 'Median Household Income'))
avg_MHV = alt.Chart(df).mark_rule(strokeDash=[4,4], opacity = 0.8).encode(alt.Y('mean(Median_HV):Q', title = 'Median Home Value'))

avg_MHV_text = alt.Chart(df).mark_text(
    text = 'US Average MHV',
    baseline = 'middle',
    fontSize = 12,
    color = '#555555',
    dx = -250,
    dy = -10
).encode(
    alt.Y('mean(Median_HV):Q')
)

avg_MHI_text = alt.Chart(df).mark_text(
    text = 'US Average MHI',
    baseline = 'middle',
    fontSize = 12,
    color = '#555555',
    dx = 200,
    dy = 10,
    angle = 270
).encode(
    alt.X('mean(Median_HI):Q')
)

quad = alt.Chart(df).mark_rect(fill ='#dddddd', fillOpacity = 0.1).encode(
    x=alt.value(225),
    y=alt.value(418),
    x2=alt.value(600),
    y2=alt.value(500)
)

(top_hist & (quad + all_points + point_highlight + RL_point + annotation + avg_MHI + avg_MHI_text + avg_MHV + avg_MHV_text | right_hist)).configure_view(
    stroke=None
)

alt.VConcatChart(...)

In [38]:
df2 = pd.read_csv('datasets/Unemployment_Rate.csv').dropna()
df2['Year'] = df2['Year'].astype(str).str.extract('([0-9]{4})')
df2

County_State            County           State  Year  \
0      Abbeville County, SC  Abbeville County  South Carolina  2010   
1      Abbeville County, SC  Abbeville County  South Carolina  2011   
2      Abbeville County, SC  Abbeville County  South Carolina  2012   
3      Abbeville County, SC  Abbeville County  South Carolina  2013   
4      Abbeville County, SC  Abbeville County  South Carolina  2014   
...                     ...               ...             ...   ...   
18836    Ziebach County, SD    Ziebach County    South Dakota  2011   
18837    Ziebach County, SD    Ziebach County    South Dakota  2012   
18838    Ziebach County, SD    Ziebach County    South Dakota  2013   
18839    Ziebach County, SD    Ziebach County    South Dakota  2014   
18840    Ziebach County, SD    Ziebach County    South Dakota  2015   

       Unemployment_Rate  
0                   13.8  
1                   12.3  
2                   10.4  
3                    9.3  
4                    7.5  
...                  ...  
18836                6.3  
18837                6.6  
18838                6.1  
18839                5.7  
18840                5.0  

[18840 rows x 5 columns]

In [39]:
df3 = pd.read_csv('datasets/Poverty_Rate.csv').dropna()
df3['Year'] = df3['Year'].astype(str).str.extract('([0-9]{4})')
df3

State       County     County_State  Year  Poverty_Rate
0       ID   Ada County   Ada County, ID  2010          13.8
1       ID   Ada County   Ada County, ID  2011          12.3
2       ID   Ada County   Ada County, ID  2012          11.0
3       ID   Ada County   Ada County, ID  2013          10.1
4       ID   Ada County   Ada County, ID  2014          11.9
...    ...          ...              ...   ...           ...
4843    AZ  Yuma County  Yuma County, AZ  2011          21.8
4844    AZ  Yuma County  Yuma County, AZ  2012          21.6
4845    AZ  Yuma County  Yuma County, AZ  2013          17.8
4846    AZ  Yuma County  Yuma County, AZ  2014          22.4
4847    AZ  Yuma County  Yuma County, AZ  2015          20.5

[4848 rows x 5 columns]

In [40]:
df4 = pd.read_csv('datasets/Natural_Amenities.csv')
df4

id State             County           County_State  Jan_temp  \
0      1001    AL     Autauga County     Autauga County, AL   1.20277   
1      1003    AL     Baldwin County     Baldwin County, AL   1.57504   
2      1005    AL     Barbour County     Barbour County, AL   1.31859   
3      1007    AL        Bibb County        Bibb County, AL   0.98768   
4      1009    AL      Blount County      Blount County, AL   0.74778   
...     ...   ...                ...                    ...       ...   
3106  56037    WY  Sweetwater County  Sweetwater County, WY  -1.13009   
3107  56039    WY       Teton County       Teton County, WY  -1.77535   
3108  56041    WY       Uinta County       Uinta County, WY  -1.23763   
3109  56043    WY    Washakie County    Washakie County, WY  -1.45272   
3110  56045    WY      Weston County      Weston County, WY  -0.82401   

      Jan_sun  Jul_temp  Jul_sun     Land  Water_area  Scale   Rank  
0    -0.64758  -0.13206 -0.68502  0.77701     0.26585   0.78      4  
1     0.01482   0.36308 -1.09576 -0.73966     1.70428   1.82      4  
2     0.01482  -0.01148 -0.89039 -0.73966     0.49570   0.19      4  
3    -0.64758  -0.30223 -0.68502  0.77701    -0.27812  -0.15      3  
4    -0.64758   0.09330 -0.68502  0.77701    -0.05592   0.23      4  
...       ...       ...      ...      ...         ...    ...    ...  
3106  0.52667   0.88070  2.19018  0.32201    -0.15981   2.63      5  
3107 -0.43682   2.89768  1.91635  1.83868     0.94589   5.39      6  
3108  0.52667   2.24757  2.19018  0.17034    -0.58134   3.32      5  
3109  0.46645  -0.34251  1.77944  1.68702    -1.03595   1.10      4  
3110  0.13526  -0.09123  1.02641  0.01867    -1.17586  -0.91      3  

[3111 rows x 12 columns]

In [41]:
#### Vis2 - Unemployment Rate and Poverty Rate

# Interactions
selection = alt.selection_single(fields = ['County_State'],empty = 'none')
hover = alt.selection_single(on = 'mouseover',empty = 'none')

# Bar Chart - Natural Amenities Ranking
rank_bars = alt.Chart(df4).mark_bar().encode(
    alt.X('County_State:N', 
          sort = alt.EncodingSortField(field = 'Scale', order = 'descending'),
          axis = alt.Axis(labels = False, title = None, tickSize = 0, domainOpacity = 0)
         ),
    alt.Y('Scale:Q', 
          axis = alt.Axis(labels = False, gridOpacity = 0, tickSize = 0, domainOpacity = 0, title = '')
         ),
    color=alt.condition(
        alt.datum.Scale > 0,
        alt.value("#ecca96"),  # The positive color
        alt.value("#d18954")  # The negative color
    )
).transform_window(
    sort = [alt.SortField('Scale', order = 'descending')],
    scale_rank = 'rank(*)'
).transform_filter(
    (alt.datum.scale_rank <= 10) | (alt.datum.scale_rank > 3101)
).properties(
    width = 600,
    height = 385,
    title = {
        'text': 'Natural Amenities Scale Ranking by County',
        'subtitle': 'Top 10 and Last 10 Counties',
        'align': 'left',
        'dx': -350
    }
)

line = alt.Chart(df4).mark_rule(opacity = 0.8, strokeWidth = 0.4).encode(alt.Y('Scale:Q')).transform_filter(alt.datum.Scale == 0)

base_bars = rank_bars.add_selection(selection).add_selection(
    hover
).encode(
    opacity = alt.condition(hover, alt.value(1), alt.value(0.6)),
    stroke = alt.condition(hover, alt.value('black'), alt.value('white'))
)

bar_highlight = rank_bars.encode(
    opacity = alt.condition(selection, alt.value(1), alt.value(0.6))).transform_filter(selection)

#bg = alt.Chart(df4).mark_rect(fill ='#f2f2f2', fillOpacity = 0.1).encode(
    #x=alt.value(0),
    #y=alt.value(0),
    #x2=alt.value(500),
    #y2=alt.value(350)
#)

county_pos = alt.Chart(df4).mark_text(
    angle = 315,
    align = 'right',
    baseline = 'bottom',
    fontSize = 10,
    dx = -30,
    dy = 40
).encode(
    alt.X('County_State:N',sort = alt.EncodingSortField(field = 'Scale', order = 'descending')),
    text = 'County_State',
    opacity = alt.condition(selection, alt.value(1), alt.value(0.6))
).transform_window(
    sort = [alt.SortField('Scale', order = 'descending')],
    scale_rank = 'rank(*)'
).transform_filter(
    alt.datum.scale_rank <=10
)

county_neg = alt.Chart(df4).mark_text(
    angle = 315,
    align = 'left',
    baseline = 'bottom',
    fontSize = 10,
    dx = -25,
    dy = 24
).encode(
    alt.X('County_State:N',sort = alt.EncodingSortField(field = 'Scale', order = 'descending')),
    text = 'County_State',
    opacity = alt.condition(selection, alt.value(1), alt.value(0.6))
).transform_window(
    sort = [alt.SortField('Scale', order = 'descending')],
    scale_rank = 'rank(*)'
).transform_filter(
    alt.datum.scale_rank > 3101
)

scale_pos = alt.Chart(df4).mark_text(
    baseline = 'bottom',
    fontSize = 10,
    dy = -5
).encode(
    alt.X('County_State:N',sort = alt.EncodingSortField(field = 'Scale', order = 'descending')),
    alt.Y('Scale:Q'),
    text = 'Scale',
    opacity = alt.condition(selection, alt.value(1), alt.value(0.6))
).transform_window(
    sort = [alt.SortField('Scale', order = 'descending')],
    scale_rank = 'rank(*)'
).transform_filter(
    alt.datum.scale_rank <=10
)

scale_neg = alt.Chart(df4).mark_text(
    baseline = 'bottom',
    fontSize = 10,
    dy = 15
).encode(
    alt.X('County_State:N',sort = alt.EncodingSortField(field = 'Scale', order = 'descending')),
    alt.Y('Scale:Q'),
    text = 'Scale',
    opacity = alt.condition(selection, alt.value(1), alt.value(0.6))
).transform_window(
    sort = [alt.SortField('Scale', order = 'descending')],
    scale_rank = 'rank(*)'
).transform_filter(
    alt.datum.scale_rank > 3101
)

county_text = county_pos + scale_pos + county_neg + scale_neg

# Boxplot - Unemployment Rate & Poverty Rate
def boxplot(data, y_axis, color, title):
    box = altcat.catplot(data, width = 180, height = 350,
                   mark = dict(type = 'point', color = color),
                   box_mark = dict(size = 17, strokeWidth = 1, opacity = 0.6, color = color),
                   whisker_mark = dict(width = 17, strokeWidth = 0.8, opacity = 0.7),
                   encoding = dict(x = alt.X('Year:N', 
                                             axis = alt.Axis(tickOpacity = 0, labelAngle = 0, title = '')),
                                   y = alt.Y(y_axis, 
                                             scale = alt.Scale(zero = False),
                                             axis = alt.Axis(tickMinStep = 5, 
                                                             gridOpacity = 0.5, 
                                                             tickOpacity = 0, 
                                                             domainOpacity = 0,
                                                             title = '')),
                                   ),
                   transform = "box"
                   ).properties(
                            title={
                              "text": title, 
                              "subtitle": '(2010 - 2015)'
                            })
    
    line_RL = alt.Chart(data).mark_line(color = '#dd4b5f').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(alt.datum.County == 'Red Lake County')

    point_RL = alt.Chart(data).mark_point(fill = 'white', color = '#dd4b5f').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(alt.datum.County == 'Red Lake County')
    
    text_RL = alt.Chart(data).mark_text(color = '#dd4b5f', opacity = 0.6, dy = 20, dx = -15, fontSize = 13, fontWeight = 500).encode(
        alt.X('Year:O'),
        alt.Y(y_axis),
        text = 'County_State'
    ).transform_filter((alt.datum.County == 'Red Lake County') & (alt.datum.Year == '2014'))
    
    lines = alt.Chart(data).mark_line(color = '#f2a952').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(selection)
    
    points = alt.Chart(data).mark_point(fill = 'white', color = '#f2a952').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(selection)
    
    texts = alt.Chart(data).mark_text(color = '#f2a952', opacity = 0.8, dy = -25, dx = 30, fontSize = 13, fontWeight = 500).encode(
        alt.X('Year:O'),
        alt.Y(y_axis),
        text = 'County_State'
    ).transform_filter(selection).transform_filter(alt.datum.Year == '2011')
    
    return box + line_RL + point_RL + lines + points + text_RL + texts

box_unemp = boxplot(df2, 'Unemployment_Rate:Q', '#55b9cf', 'County Unemployment Rate')
box_pov = boxplot(df3, 'Poverty_Rate:Q', '#a6d753', 'County Poverty Rate')

(base_bars + bar_highlight + county_text + line | (box_unemp | box_pov)).configure_view(
    strokeWidth=0
)

alt.HConcatChart(...)

In [42]:
df5 = pd.read_csv('datasets/Farm_Earn_MN.csv')
df5

id                County_State                  County  Year  \
0     27001           Aitkin County, MN           Aitkin County  2001   
1     27001           Aitkin County, MN           Aitkin County  2002   
2     27001           Aitkin County, MN           Aitkin County  2003   
3     27001           Aitkin County, MN           Aitkin County  2004   
4     27001           Aitkin County, MN           Aitkin County  2005   
...     ...                         ...                     ...   ...   
1300  27173  Yellow Medicine County, MN  Yellow Medicine County  2011   
1301  27173  Yellow Medicine County, MN  Yellow Medicine County  2012   
1302  27173  Yellow Medicine County, MN  Yellow Medicine County  2013   
1303  27173  Yellow Medicine County, MN  Yellow Medicine County  2014   
1304  27173  Yellow Medicine County, MN  Yellow Medicine County  2015   

      Farm_Earnings  
0              1900  
1              3189  
2              3723  
3              2601  
4              1052  
...             ...  
1300          84588  
1301          90487  
1302          85914  
1303          42691  
1304          73204  

[1305 rows x 5 columns]

In [43]:
df6 = pd.read_csv('datasets/GDP_Growth.csv')
df6

id                  County                County_State  Year  \
0     27001           Aitkin County           Aitkin County, MN  2002   
1     27001           Aitkin County           Aitkin County, MN  2003   
2     27001           Aitkin County           Aitkin County, MN  2004   
3     27001           Aitkin County           Aitkin County, MN  2005   
4     27001           Aitkin County           Aitkin County, MN  2006   
...     ...                     ...                         ...   ...   
1213  27173  Yellow Medicine County  Yellow Medicine County, MN  2011   
1214  27173  Yellow Medicine County  Yellow Medicine County, MN  2012   
1215  27173  Yellow Medicine County  Yellow Medicine County, MN  2013   
1216  27173  Yellow Medicine County  Yellow Medicine County, MN  2014   
1217  27173  Yellow Medicine County  Yellow Medicine County, MN  2015   

      GDP_Growth_Percentage  
0                       9.0  
1                       1.1  
2                       9.1  
3                      10.8  
4                      -1.9  
...                     ...  
1213                   11.5  
1214                   -2.2  
1215                    5.2  
1216                   -2.5  
1217                   22.4  

[1218 rows x 5 columns]

In [44]:
df7 = pd.read_csv('datasets/Farm_Earnings_Percentage.csv')
df7

id                  County                County_State  Year  \
0     27001           Aitkin County           Aitkin County, MN  2002   
1     27001           Aitkin County           Aitkin County, MN  2003   
2     27001           Aitkin County           Aitkin County, MN  2004   
3     27001           Aitkin County           Aitkin County, MN  2005   
4     27001           Aitkin County           Aitkin County, MN  2006   
...     ...                     ...                         ...   ...   
1213  27173  Yellow Medicine County  Yellow Medicine County, MN  2011   
1214  27173  Yellow Medicine County  Yellow Medicine County, MN  2012   
1215  27173  Yellow Medicine County  Yellow Medicine County, MN  2013   
1216  27173  Yellow Medicine County  Yellow Medicine County, MN  2014   
1217  27173  Yellow Medicine County  Yellow Medicine County, MN  2015   

      Farm_Earn_Percentage  Total_Earnings  Farm_Earnings  Nonfarm_Earnings  \
0                     2.03          157037           3189            153848   
1                     2.25          165604           3723            161881   
2                     1.49          174543           2601            171942   
3                     0.60          174266           1052            173214   
4                     0.87          178383           1544            176839   
...                    ...             ...            ...               ...   
1213                 26.87          314848          84588            230260   
1214                 28.31          319641          90487            229154   
1215                 26.99          318325          85914            232411   
1216                 14.54          293539          42691            250848   
1217                 20.44          358105          73204            284901   

      Unnamed: 8  Unnamed: 9  
0            NaN         NaN  
1            NaN         NaN  
2            NaN         NaN  
3            NaN         NaN  
4            NaN         NaN  
...          ...         ...  
1213         NaN         NaN  
1214         NaN         NaN  
1215         NaN         NaN  
1216         NaN         NaN  
1217         NaN         NaN  

[1218 rows x 10 columns]

In [45]:
#### Vis3 - Farm Earnings Percentage and GDP Growth

# Interactions
counties = alt.topo_feature(data.us_10m.url, 'counties')
selection = alt.selection_single(on = 'mouseover',empty = 'none')
selectCounty = alt.selection_single(fields = ['County_State'],empty = 'none')

# US map
map = alt.Chart(counties).mark_geoshape(stroke = 'white', strokeWidth = 0.25).encode(
    color = alt.Color('Scale:Q', 
                      scale = alt.Scale(range = ['#a0651a','#f2e9d0','#a2d9d1']),
                      legend = alt.Legend(orient ='none',
                                          legendX = 200,legendY = 0,
                                          direction = 'horizontal', 
                                          title = 'Natural Amenities Scale',
                                          titleAnchor = 'middle',
                                          gradientLength = 160)),
    tooltip = [alt.Tooltip('County_State:N', title = 'County'), alt.Tooltip('Scale:Q', title = 'Natural Amenities Scale')]
).transform_lookup(
    lookup = 'id',
    from_ = alt.LookupData(df4, 'id', ['Scale','County_State'])
).project(
    type = 'albersUsa'
).properties(
    width = 400,
    height = 500
).add_selection(
    selection
).add_selection(
    selectCounty
).encode(
    stroke = alt.condition(selection, alt.value('black'), alt.value('white'))
).transform_calculate(
    state_id = "(datum.id / 1000)|0"
).transform_filter(
    (alt.datum.state_id) == 27
)

# Line Chart(Farm Earnings and GDP Growth)
line_chart_farm = alt.Chart(df7).mark_line().encode(
    alt.X('Year:N', axis = alt.Axis(tickOpacity = 0, labelAngle = 315, title = '')),
    alt.Y('Farm_Earn_Percentage:Q', scale=alt.Scale(domain=[-10, 50]), axis = alt.Axis(tickOpacity = 0, title = 'Farm Earnings Percentage (%)', domainOpacity = 0))
).properties(
    width = 450,
    height = 215
).transform_filter(selectCounty) #.transform_filter(alt.datum.County == 'Red Lake County')

line_chart_GDP = alt.Chart(df6).mark_line().encode(
    alt.X('Year:N', axis = alt.Axis(tickOpacity = 0, labelAngle = 315, title = '')),
    alt.Y('GDP_Growth_Percentage:Q', scale=alt.Scale(domain=[-50, 70]), axis = alt.Axis(tickOpacity = 0, title = 'GDP Growth (%)', domainOpacity = 0))
).properties(
    width = 450,
    height = 215
).transform_filter(selectCounty)

def marks(data, y_axis):
    line_RL = alt.Chart(data).mark_line(color = '#dd4b5f').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(alt.datum.County == 'Red Lake County')

    point_RL = alt.Chart(data).mark_point(fill = 'white', color = '#dd4b5f').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(alt.datum.County == 'Red Lake County')
    
    text_RL = alt.Chart(data).mark_text(color = '#dd4b5f', opacity = 0.6, dy = 20, dx = -15, fontSize = 13, fontWeight = 500).encode(
        alt.X('Year:O'),
        alt.Y(y_axis),
        text = 'County_State'
    ).transform_filter((alt.datum.County == 'Red Lake County') & (alt.datum.Year == 2014))
    
    lines = alt.Chart(data).mark_line(color = '#f2a952').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(selectCounty)
    
    points = alt.Chart(data).mark_point(fill = 'white', color = '#f2a952').encode(
        alt.X('Year:O'),
        alt.Y(y_axis)
    ).transform_filter(selectCounty)
    
    texts = alt.Chart(data).mark_text(color = '#f2a952', opacity = 0.8, dy = 20, dx = 30, fontSize = 13, fontWeight = 500).encode(
        alt.X('Year:O'),
        alt.Y(y_axis),
        text = 'County_State'
    ).transform_filter(selectCounty).transform_filter(alt.datum.Year == 2007)
    
    return line_RL + point_RL + lines + points + text_RL + texts

mark_GDP = marks(df6, 'GDP_Growth_Percentage:Q')
mark_farm = marks(df7, 'Farm_Earn_Percentage:Q')

(map | ((line_chart_farm + mark_farm) & (line_chart_GDP + mark_GDP))).configure_view(strokeWidth = 0) 

alt.HConcatChart(...)